---

# S02E01 : Loop better - Itérateurs & génerateurs
Cyril Desjouy

---

## 1. Les itérables

Un itérable est un objet contenant plusieurs éléments qu'on peut parcourir avec une boucle `for` (par exemple). 
Les objets de type séquentiel que nous avons vu précédemment sont des itérables : les objets `list`, `tuple`, `str`, `ndarray`, ...

Les objets itérables héritent de la méthode `__iter__` qui est requise pour retourner un objet de type **itérateur**.


## 2. Les itérateurs

Un itérateur est un type objet particulier représentant un flux de données. Il hérite des méthodes spéciales :

* `__iter__`: retourne l'objet itérateur lui même (`self`). Cette méthode est requise pour que l'objet puisse être utilisé dans une boucle `for`.
* `__next__`: retourne l'élément suivant. S'il n'y a plus d'éléments, lève l'exception `StopIteration`.

Tous les itérateurs sont des objets itérables (ils possèdent la méthode `__iter__`), mais l'inverse n'est pas valable. Les objets de type `list` par exemple ne possèdent pas de méthode `__next__`. Ce sont donc des itérables mais pas des itérateurs. Il est par contre possible de construire un itérateur à partir d'un itérable à l'aide de la fonction built-in `iter`:

```python
>> iterable = [1, 2, 3]        # objet de type list qui est un itérable
>> iterator = iter(iterable)   # équivalent à iterator = iterable.__iter__()
>> type(iterable)
list                           
>> type(iterator)
list_iterator               
```
><div class="alert alert-block alert-info">
Utilisez la fonction <code>len</code> pour déterminer la longueur de l'objet <code>iterable</code> et celle de l'objet <code>iterator</code>. 
</div>


Comme vous avez pu le constater, les itérateurs n'ont pas toutes les fonctionnalités des itérables. Par exemple, ils n'ont pas de méthode `__len__`. Ils ne peuvent par ailleurs être indexés!

><div class="alert alert-block alert-info">
Utilisez maintenant la fonction <code>next</code> avec comme argument d'entrée l'objet <code>iterator</code>. Exécutez cette instruction à plusieurs reprises. Que constatez vous ? 
</div>

Lorsque l'itérateur est consommé, il n'est pas possible de le réutiliser. Nous avons déjà observé ce comportement lors de l'étude des expressions génératrices dans un précédent notebook. A chaque appel de `__next__` notre itérateur retourne une nouvelle valeur jusqu'à ce qu'il soit épuisé. Il lève alors l'exception `StopIteration`.

C'est exactement ce qui se passe dans une boucle `for`:

* La méthode `__iter__` est appelée sur l'objet à itérer, ce qui retourne un itérateur.
* La méthode `__next__` est appelée à chaque itération pour générer la prochaine valeur de l'itérateur.
* Lorsque l'itérateur est vide, l'exception `StopIteration` est levée. C'est le signal de sortie de boucle!

Notons également qu'il est possible de développer des itérateurs personnalisés relativement facilement en implémentant une **classe** contenant les méthodes spéciales `__iter__` et `__next__`. Par exemple:

```python
class Counter:
    
    def __init__(self, n):
        self.i = 0
        self.n = n

    def __iter__(self):
        return self               # Retourne l'instance elle même

    def __next__(self): 
        if self.i > self.n:
            raise StopIteration   # Quand i>n, on lève l'exception StopIteration
        else:
            self.i += 1
            return self.i - 1     # Sinon on retourne i+1 !
```

Chaque instance de cette classe est alors un itérateur:
```python
>> c = Counter(10)
>> next(c)
0
>> next(c)
1
```

**Conclusions:** Dans certains cas, en calcul scientifique la quantité de données à gérer est tellement importante qu'il n'est pas possible de la stocker en mémoire. De part leur construction, les itérateurs ont une très faible empreinte mémoire quel que soit la taille du jeu de données. Ceci leur permet de travailler sur des quantités colossales de données, voir même infinies. L'inconvénient des itérateurs est qu'une fois consommés, ils ne peuvent pas être réutilisés.

## 3. Les générateurs

### 3.1. Les fonctions génératrices

Un générateur est un itérateur. Il est généralement défini par une fonction dans laquelle l'instruction `return` est remplacée par une ou plusieurs instructions `yield`. Cette fonction est dans ce cas appelée **fonction génératrice**. Les méthodes spéciales `__iter__` et `__next__` (ce qui défini un itérateur) sont automatiquement implémentées lors de sa création. Voici un exemple de fonction génératrice:

```python
def counter():
    yield 1
    yield 2
    yield 3
```

qui permet de créer un générateur:
```python
>> c = counter()
>> type(counter)
function
>> type(c)
generator
```

><div class="alert alert-block alert-info">
Utilisez à plusieurs reprises la fonction <code>next</code> sur l'objet <code>c</code>. 
</div>

Les générateurs étant des itérateurs, ils présentent le même comportement. Une fois épuisés, ils lèvent l'exception `StopIteration` et ne peuvent pas être réutilisés.

Afin d'éviter des `yield` répétés, les fonctions génératrices utilisent souvent des boucles:
```python
def counter(n):
    for i in range(n):
        yield i
```

Il est ainsi possible de créer un générateur pouvant générer des milliards de valeurs de manière optimisée et sans surcharger la mémoire.

```python
>> c = counter(2**24)
>> c.__sizeof__()
96                                 # 96 bytes in memory
>> l = [i for i in range(2**24)]   # liste avec le même nombre d'objets que notre itérateur
>> l.__sizeof__()
146916472                          # ~147 Mb in memory !
```

Et pourquoi pas un itérateur infini ? 
```python
def counter():
    i = 0
    while True:
        i += 1
        yield i
```

```python
>> c = counter()
>> c.__sizeof__()
96
```

### 3.2. Les expressions génératrices

Le principe de fonctionnement des **fonctions génératrices** doit vous rappeler celui des **expressions génératrices** vues dans un notebook précédent. 

Pour rappel, les expressions génératrices permettent de créer des **générateurs** d'une manière plus simple et concise que les fonctions génératrices. La syntaxe des expressions génératrices est similaire à celle des compréhensions de liste mais utilise des crochets au lieu des parenthèses. En voici un exemple:

```python
s = ('hello {}'.format(i) for i in ['Bob', 'John', 'Jim', 'World!'])
```
><div class="alert alert-block alert-info">
Utilisez la fonction <code>print</code> pour afficher cette expression génératrice.
</div>

Que ce soit pour un itérateur ou un générateur, il n'est pas possible d'accéder directement aux valeurs (pas de méthode `__len__`, pas d'indexation, ...). Pour y accéder, il faut utiliser la fonction `next` ou l'itérer à l'aide d'une boule `for` !

**Note:** *Les expressions génératrices peuvent être passées en argument d'entrée de toute fonction qui accepte un itérateur. Par exemple:*

```python
sum(i**2 for i in range(10))
```

*Dans ce cas, pas besoin du second jeu de parenthèses.*

## Résumé

Les **itérateurs** sont construits à partir d'un itérable grâce à la fonction `iter` ou en développant sa propre classe implémentant les méthodes `__iter__` et `__next__`.

Les **générateurs** sont construits à partir d'une fonction utilisant l'instruction `yield` ou d'une expression génératrice.

Tout objet générateur ou itérateur est un itérable. L'inverse n'est pas nécessairement vrai.


## Application : Nombres premiers
><div class="alert alert-block alert-info">
Créer un générateur permettant de générer tous les nombres premiers de 0 à $n$, où $n$ sera un paramètre d'entrée. </div>


## Bibiographie

* [Data-flair - Genrator vs. Iterator](https://data-flair.training/blogs/python-generator-vs-iterator/)